# Alimentador obra - características

Notebook para crear los símbolos y vincularlos a las obras.  Necesita dos tablas. Una que contiene los ids de las obras a crear y otra que contiene la relación de los símbolos y obras del excel de Arca

In [1]:
import os
import json
import numpy as np
import requests
import pandas as pd
from dotenv import load_dotenv

## Abrir tablas y filtrar datos

In [4]:
load_dotenv()
config = json.load(open('../config/config.json'))

caracts_tabla = '../datos/entrada/csv/Registros_caracteristicas_particulares_2.csv'


caracts = pd.read_csv(caracts_tabla, dtype=str)
caracts = caracts.dropna(how='all')
caracts = caracts.dropna(subset=['id'])
caracts['id'] = caracts['id'].astype(int)
caracts = caracts.sort_values(by='id')

filtrar = False
if filtrar:
    obras_tabla = '../tablas/csv/obra-soluciones.csv'
    # dataframes de las tablas
    obras = pd.read_csv(obras_tabla, dtype=str)
    #filtrar los caracts por los ids de obras en arca
    caracts_filtrados = caracts.loc[caracts['artwork_id'].isin(obras['arca_id']).tolist()]

    #muestra para prueba
    #caracts_filtrados = caracts_filtrados.sample(1)
    #len(caracts_filtrados.index)
    #caracts_filtrados
    caracts = caracts_filtrados

## URLS

In [6]:
#baseurl = 'http://localhost:8055/'
baseurl = config['baseurl']
obra_caracts_baseurl = f'{baseurl}items/obra_caracteristicas_particulares_lista'
obras_url = f'{baseurl}items/obra'
caracts_url = f'{baseurl}items/caracteristicas_particulares_lista'

key = os.getenv('KEY')
headers =  {'Authorization':f'Bearer {key}'}


## Iteración

In [10]:
for index, row in caracts.iterrows():
    m2m_arcaid  = row['id']
    obra_arcaID = row['artwork_id']
    caract_arcaID = row['engraving_id']
    obra_url = f'{obras_url}?filter[arca_id][_eq]={obra_arcaID}&limit=1'
    sim_url = f'{caracts_url}?filter[arca_id][_eq]={caract_arcaID}&limit=1'
    #obra = {}
    #caract = {}

    #obtener la obra de la api
    try:
        r_obra = requests.get(obra_url)
        r_obra.raise_for_status()
        print(f'econtrada obra: {obra_arcaID}')
    except requests.RequestException as err:
        print(f'Error obteniendo obra: {obra_arcaID}')
        print(err)
        # si se produce error, continua el siguiente registro
        continue

    #se obtienen los datos de la respuesta
    try:
        obra = r_obra.json()['data'][0]
        #print(obra)
    except IndexError as e:
        print(e)
        continue

    #obtener el caract de la api
    try: 
        r_sim = requests.get(sim_url)
        r_sim.raise_for_status()
    except requests.RequestException as err:
        print(f'Error obteniendo caract: {caract_arcaID}')
        print(err)
        continue

    #se obtienen los datos de la respuesta
    try:
        caract = r_sim.json()['data'][0]
        #print(caract)
    except IndexError as e:
        print(e)
        continue

    # crear el objeto obra caract con los ids de los objetos viculados
    obra_sim = {}
    obra_sim['arca_id'] = m2m_arcaid 
    obra_sim['obra_id'] = obra['id']
    obra_sim['caracteristicas_particulares_lista_id'] = caract['id']
    
    # crear m2m obra caract
    try:
        r_obsim_m2m = requests.post(obra_caracts_baseurl, json = obra_sim, headers=headers)
        r_obsim_m2m.raise_for_status()
    except requests.RequestException as err:
        print(f'Error creando m2m obra caract: {obra_sim}')
        print(err)
        continue

    obsim_m2m = r_obsim_m2m.json()['data']
    m2mid = obsim_m2m['id']
    print(f'Creada relacion obra caract: {m2mid} arcaid: {m2m_arcaid}')
    #print(obsim_m2m)
    

econtrada obra: 6367
Creada relacion obra caract: 1 arcaid: 2
econtrada obra: 6367
Creada relacion obra caract: 2 arcaid: 3
econtrada obra: 2964
Creada relacion obra caract: 3 arcaid: 5
econtrada obra: 2964
Creada relacion obra caract: 4 arcaid: 6
econtrada obra: 3906
Creada relacion obra caract: 5 arcaid: 7
econtrada obra: 3906
Creada relacion obra caract: 6 arcaid: 8
econtrada obra: 3906
Creada relacion obra caract: 7 arcaid: 9
econtrada obra: 3906
Creada relacion obra caract: 8 arcaid: 10
econtrada obra: 3906
Creada relacion obra caract: 9 arcaid: 11
econtrada obra: 3906
Creada relacion obra caract: 10 arcaid: 12
econtrada obra: 14765
Creada relacion obra caract: 11 arcaid: 13
econtrada obra: 14765
Creada relacion obra caract: 12 arcaid: 14
econtrada obra: 14765
Creada relacion obra caract: 13 arcaid: 15
econtrada obra: 14765
Creada relacion obra caract: 14 arcaid: 16
econtrada obra: 14765
Creada relacion obra caract: 15 arcaid: 17
econtrada obra: 14765
Creada relacion obra caract: 